In [ ]:
pip install haystack-ai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 380.0/380.0 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.4/89.4 kB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.4/54.4 kB 4.6 MB/s eta 0:00:00


In [ ]:
import pandas as pd

In [ ]:
from haystack import Document
from haystack import Pipeline
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.components.writers import DocumentWriter
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever

In [ ]:
from google.colab import drive
drive.mount('/content/drive')
file_path = '/content/drive/My Drive/df_for_LLM_v2.csv'
df_for_LLM = pd.read_csv(file_path)

Mounted at /content/drive


In [ ]:
df_for_LLM

name  \
0                       San Carlos   
1                    Angel's salon   
2             La Casa del Plastico   
3                     EPA Solarium   
4                    Policia Upala   
..                             ...   
143                Coopeguanacaste   
144  Liberia International Airport   
145                 Playa del Coco   
146                     Mega Super   
147                      Zi Lounge   

                                    property_tag_old_2  \
0                                       Hardware Store   
1                                           Beauty Bar   
2                                     Department Store   
3                     Department Store, Hardware Store   
4              Police Department, Information Services   
..                                                 ...   
143                                          Utilities   
144                                            Airport   
145                                            Beaches   
146                                        Supermarket   
147  Restaurant, Bar, International, Seafood, Pizza...   

                            property_email  \
0              mmora@depositosancarlos.com   
1                   myrnaangel@hotmail.com   
2               info@lacasadelplastico.com   
3                      contacto@xr.epa.biz   
4                 no information available   
..                                     ...   
143  servicioalcliente@coopeguanacaste.com   
144           \ninfo@guanacasteairport.com   
145               no information available   
146               no information available   
147                      info@zilounge.com   

                           property_hours_of_operation property_location  \
0    Monday - Friday 7:00 AM- 5:00 PM, Saturday 7:0...    Playa del Coco   
1    Monday 9:00 AM - 6:00 PM, Tuesday - Saturday 9...    Playa del Coco   
2    Monday - Saturday 8:00 AM - 6:00 PM, Sunday  C...    Playa del Coco   
3    Monday - Friday 9:00 AM - 5:00 PM, Saturday 9:...           Liberia   
4    Monday - Friday 8:00 AM - 4:00 PM, Saturday - ...          Canalete   
..                                                 ...               ...   
143  Monday - Saturday 7:00 AM - 5:00 PM,\nSunday  ...    Playa del Coco   
144                 Monday - Sunday 6:00 AM - 12:00 AM           Liberia   
145                           no information available    Playa del Coco   
146  Monday - Saturday 7:00 AM - 10:00 PM Sunday 7:...    Playa del Coco   
147                 Monday - Sunday 11:00 AM - 2:30 AM    Playa del Coco   

                                  property_description  \
0    Deposito San Carlos is a largest building mate...   
1    Angel's Salon is a professional hair and beaut...   
2    La Casa del Plastico specializes in the sale o...   
3    EPA Solarium - Hardware and Home Goods Store o...   
4    Policia Upala - Police Department and Informat...   
..                                                 ...   
143  Coopeguanacaste R.L. is a cooperative in Guana...   
144  Daniel Oduber Quirós International Airport (LI...   
145  Playas del Coco is a vibrant hub of activity, ...   
146  Mega Super offers a wide range of products, fr...   
147  In this bar-restaurant, there are dishes and d...   

        property_phone_number  \
0              +506 2670-1211   
1    no information available   
2              +506 2670-0700   
3    no information available   
4              +506 2470-0235   
..                        ...   
143            +506 2681-4700   
144            +506 2666-9600   
145  no information available   
146            +506 2670-1239   
147            +506 8888-3939   

                                         combined_text  
0    San Carlos, Hardware Store, mmora@depositosanc...  
1    Angel's salon, Beauty Bar, myrnaangel@hotmail....  
2    La Casa del Plastico, Department Store, info@l...  
3    EPA Solarium, Department Store, Hardware Store...  
4    Policia Upala, Police Depa

In [ ]:
# Пример №3, в контенте combined_text то есть содержимое всех столбцов
documents = [
    Document(
        content=f"{row['combined_text']}",

    )
    for _, row in df_for_LLM.iterrows()
]

In [ ]:
# Создаем DocumentStore
document_store = InMemoryDocumentStore()

# Добавляем документы в DocumentStore
document_store.write_documents(documents)

# Создаем InMemoryEmbeddingRetriever
retriever = InMemoryEmbeddingRetriever(document_store=document_store)

In [ ]:
qa_pipeline = Pipeline()

In [ ]:
retriever = InMemoryBM25Retriever(document_store=document_store)
qa_pipeline.add_component(instance=retriever, name="retriever")

In [ ]:
qa_pipeline.add_component(instance=ExtractiveReader(model="deepset/deberta-v3-base-squad2"), name="reader")

In [ ]:
qa_pipeline.connect("retriever", "reader")

🚅 Components
  - retriever: InMemoryBM25Retriever
  - reader: ExtractiveReader
🛤️ Connections
  - retriever.documents -> reader.documents (List[Document])

In [ ]:
query = "When is open the restaurant Zi Lounge?"
qa_pipeline.run(
    data={"retriever": {"query": query, "top_k": 3}, "reader": {"query": query, "top_k": 3}}
)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/992 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/735M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/379 [00:00<?, ?B/s]

spm.model:   0%|          | 0.00/2.46M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/8.65M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/173 [00:00<?, ?B/s]

{'reader': {'answers': [ExtractedAnswer(query='When is open the restaurant Zi Lounge?', score=0.757442057132721, data=' Monday - Sunday 11:00 AM - 2:30 AM', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 19.801461834952015), context=None, document_offset=ExtractedAnswer.Span(start=125, end=160), context_offset=None, meta={}),
   ExtractedAnswer(query='When is open the restaurant Zi Lounge?', score=0.48066219687461853, data=' Monday - Saturday 4:00 PM - 12:00 AM, Sunday - Closed', document=Document(id=829cb8c526265bc03477b109eb89acda01db27d62b51c8fa586ca3c63ec56afd, content: 'Zarpe, Bar, Cocktails, Alcohol, LASENORA@ZARPE.BAR, Monday - Saturday 4:00 PM - 12:00 AM, Sunday - C...', score: 16.35872539077387), context=None, document_offset=ExtractedAnswer.Span(start=51, end=105), context_offset=None, meta={}),
   ExtractedAnswer(q

In [ ]:
file_path = '/content/drive/My Drive/QA dataset from LLMs.xlsx'
QA_dataset_from_LLMs = pd.read_excel(file_path)

In [ ]:
pd.set_option('display.max_colwidth', None)

In [ ]:
QA_dataset_from_LLMs

Questions  \
0                                         1. "What Italian restaurants are there in Playa Hermosa?"   
1                                        2. "What American-style restaurants are there in Liberia?"   
2                                         3. "What French restaurants are there in Playa del Coco?"   
3                                  4. "What vegan-friendly restaurants are there in Playa Hermosa?"   
4                                          5. "What Asian restaurants are there in Playa del Coco?"   
5                                                      6. "What cafes are there in Playa del Coco?"   
6                                              7. "What entertainment venues are there in Liberia?"   
7                  8. "Where can I find beauty or service-related establishments in Playa Hermosa?"   
8                                           9. "What beachfront cafes are there in Playa del Coco?"   
9                   10. "Where can I find entertainment venues with beach access in Playa Hermosa?"   
10                                            11. "What cafes near the beach are there in Liberia?"   
11                12. "Where can I find beauty and spa services with a sea view in Playa del Coco?"   
12                      13. "What family-friendly entertainment venues are there in Playa Hermosa?"   
13                         14. "What restaurants in Playa del Coco are open late into the evening?"   
14                            15. "Which establishments in Playa Ocotal open early in the morning?"   
15                                          16. "Which cafes are open right now in Playa del Coco?"   
16                                             17. "Where can I find a good gift shop in San José?"   
17                                            18. "What are some good places to visit in San José?"   
18                                    19. "Are there any good places to buy souvenirs in San José?"   
19                                           20. "What are some popular art galleries in San José?"   
20                             21. "What are some popular places to visit in San José for culture?"   
21                          22. "What are some popular places to go for entertainment in San José?"   
22                           23. "What are some popular places to visit in Puntarenas for culture?"   
23                                     24. "What are some popular places to visit in Puerto Viejo?"   
24                                                        25. "What are some popular bars in Jacó?"   
25                                          26. "What are some popular shopping centers in Escazú?"   
26                                                 27. "What are some popular theaters in Cartago?"   
27                                                 28. "What are some popular nightclubs in Limón?"   
28                                                   29. "What are some popular parks in Alajuela?"   
29                       30. "What are some popular beaches in Jacó that are suitable for surfing?"   
30                 31. "What are some popular coffee shops in Heredia that serve specialty coffee?"   
31                           32. "What are some popular nightclubs in Limón that play Latin music?"   
32                            33. "What are some popular parks in Alajuela that have a playground?"   
33                          34. "What are some popular theaters in Cartago that host performances?"   
34            35. "What are some popular shopping centers in Escazú that have a variety of stores?"   
35                36. "What are some popular coffee shops in San José that serve specialty coffee?"   
36           37. "What are some popular restaurants in Tamarindo that serve international cuisine?"   
37                         38. "What are some popular coffee shops in Heredia that serve pastries?"   
38                                39. "What are some popular parks in Ala

In [ ]:
qa_pipeline.run(data={"retriever": {"query": QA_dataset_from_LLMs['Questions'][0],"top_k": 3}, "reader": {"query": QA_dataset_from_LLMs['Questions'][0], "top_k":3}})

{'reader': {'answers': [ExtractedAnswer(query='1. "What Italian restaurants are there in Playa Hermosa?"', score=0.5491390228271484, data=' Restaurants and bars', document=Document(id=ce605dad4f840feeb7c1b30517b8ae07a9997ddc8b12cb2700ca3614a2c2a046, content: 'Playa Hermosa, Beaches, no information available, no information available, Playa Hermosa, Playa Her...', score: 19.061921898162307), context=None, document_offset=ExtractedAnswer.Span(start=437, end=458), context_offset=None, meta={}),
   ExtractedAnswer(query='1. "What Italian restaurants are there in Playa Hermosa?"', score=0.4181205928325653, data=' Pizza, Pasta', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 18.382970355806773), context=None, document_offset=ExtractedAnswer.Span(start=51, end=64), context_offset=None, meta={}),
   ExtractedAnswer(query='1. "What It

In [ ]:
algo_answers = []
for question in QA_dataset_from_LLMs['Questions']:
    # Запуск алгоритма для получения ответа
    result = qa_pipeline.run(data={"retriever": {"query": question, "top_k": 3},
                                   "reader": {"query": question, "top_k": 3}})
    # Добавление ответа в список
    algo_answers.append(result)

In [ ]:
algo_answers

[{'reader': {'answers': [ExtractedAnswer(query='1. "What Italian restaurants are there in Playa Hermosa?"', score=0.5491390228271484, data=' Restaurants and bars', document=Document(id=ce605dad4f840feeb7c1b30517b8ae07a9997ddc8b12cb2700ca3614a2c2a046, content: 'Playa Hermosa, Beaches, no information available, no information available, Playa Hermosa, Playa Her...', score: 19.061921898162307), context=None, document_offset=ExtractedAnswer.Span(start=437, end=458), context_offset=None, meta={}),
    ExtractedAnswer(query='1. "What Italian restaurants are there in Playa Hermosa?"', score=0.4181205928325653, data=' Pizza, Pasta', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 18.382970355806773), context=None, document_offset=ExtractedAnswer.Span(start=51, end=64), context_offset=None, meta={}),
    ExtractedAnswer(query='1. "What

In [ ]:
QA_dataset_from_LLMs['algo_answers'] = algo_answers

In [ ]:
QA_dataset_from_LLMs

Questions  \
0                                         1. "What Italian restaurants are there in Playa Hermosa?"   
1                                        2. "What American-style restaurants are there in Liberia?"   
2                                         3. "What French restaurants are there in Playa del Coco?"   
3                                  4. "What vegan-friendly restaurants are there in Playa Hermosa?"   
4                                          5. "What Asian restaurants are there in Playa del Coco?"   
5                                                      6. "What cafes are there in Playa del Coco?"   
6                                              7. "What entertainment venues are there in Liberia?"   
7                  8. "Where can I find beauty or service-related establishments in Playa Hermosa?"   
8                                           9. "What beachfront cafes are there in Playa del Coco?"   
9                   10. "Where can I find entertainment venues with beach access in Playa Hermosa?"   
10                                            11. "What cafes near the beach are there in Liberia?"   
11                12. "Where can I find beauty and spa services with a sea view in Playa del Coco?"   
12                      13. "What family-friendly entertainment venues are there in Playa Hermosa?"   
13                         14. "What restaurants in Playa del Coco are open late into the evening?"   
14                            15. "Which establishments in Playa Ocotal open early in the morning?"   
15                                          16. "Which cafes are open right now in Playa del Coco?"   
16                                             17. "Where can I find a good gift shop in San José?"   
17                                            18. "What are some good places to visit in San José?"   
18                                    19. "Are there any good places to buy souvenirs in San José?"   
19                                           20. "What are some popular art galleries in San José?"   
20                             21. "What are some popular places to visit in San José for culture?"   
21                          22. "What are some popular places to go for entertainment in San José?"   
22                           23. "What are some popular places to visit in Puntarenas for culture?"   
23                                     24. "What are some popular places to visit in Puerto Viejo?"   
24                                                        25. "What are some popular bars in Jacó?"   
25                                          26. "What are some popular shopping centers in Escazú?"   
26                                                 27. "What are some popular theaters in Cartago?"   
27                                                 28. "What are some popular nightclubs in Limón?"   
28                                                   29. "What are some popular parks in Alajuela?"   
29                       30. "What are some popular beaches in Jacó that are suitable for surfing?"   
30                 31. "What are some popular coffee shops in Heredia that serve specialty coffee?"   
31                           32. "What are some popular nightclubs in Limón that play Latin music?"   
32                            33. "What are some popular parks in Alajuela that have a playground?"   
33                          34. "What are some popular theaters in Cartago that host performances?"   
34            35. "What are some popular shopping centers in Escazú that have a variety of stores?"   
35                36. "What are some popular coffee shops in San José that serve specialty coffee?"   
36           37. "What are some popular restaurants in Tamarindo that serve international cuisine?"   
37                         38. "What are some popular coffee shops in Heredia that serve pastries?"   
38                                39. "What are some popular parks in Ala

In [ ]:
QA_dataset_from_LLMs.to_excel('QA_dataset_Deberta.xlsx', index=False)

Работа алгоритма неудовлетворительная на данных вопросах. Он подходит только для очень простых вопросов. Причем если нужно искать только в одной строке, то есть в одном документе.

In [ ]:
qa_pipeline.add_component(instance=ExtractiveReader(model="sjrhuschlee/flan-t5-base-squad2"), name="reader")

In [ ]:
qa_pipeline.connect("retriever", "reader")

🚅 Components
  - retriever: InMemoryBM25Retriever
  - reader: ExtractiveReader
🛤️ Connections
  - retriever.documents -> reader.documents (List[Document])

In [ ]:
query = "What are the opening hours of the restaurant Zi Lounge?"
qa_pipeline.run(
    data={"retriever": {"query": query, "top_k": 3}, "reader": {"query": query, "top_k": 3}}
)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.63k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/2.35k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/21.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.23k [00:00<?, ?B/s]

{'reader': {'answers': [ExtractedAnswer(query='What are the opening hours of the restaurant Zi Lounge?', score=0.7922326326370239, data=' Monday - Sunday 11:00 AM - 2:30 AM', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 25.75866793740871), context=None, document_offset=ExtractedAnswer.Span(start=125, end=160), context_offset=None, meta={}),
   ExtractedAnswer(query='What are the opening hours of the restaurant Zi Lounge?', score=0.7362217903137207, data=' Monday - Saturday 4:00 PM - 12:00 AM', document=Document(id=829cb8c526265bc03477b109eb89acda01db27d62b51c8fa586ca3c63ec56afd, content: 'Zarpe, Bar, Cocktails, Alcohol, LASENORA@ZARPE.BAR, Monday - Saturday 4:00 PM - 12:00 AM, Sunday - C...', score: 20.38204179149279), context=None, document_offset=ExtractedAnswer.Span(start=51, end=88), context_offset=None, meta={}),
   Ex

In [ ]:
query = "What are the opening days and hours of the restaurant Zi Lounge?"
qa_pipeline.run(
    data={"retriever": {"query": query, "top_k": 3}, "reader": {"query": query, "top_k": 3}}
)

{'reader': {'answers': [ExtractedAnswer(query='What are the opening days and hours of the restaurant Zi Lounge?', score=0.7985390424728394, data=' Monday - Sunday 11:00 AM - 2:30 AM', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 25.88915923886433), context=None, document_offset=ExtractedAnswer.Span(start=125, end=160), context_offset=None, meta={}),
   ExtractedAnswer(query='What are the opening days and hours of the restaurant Zi Lounge?', score=0.7638328075408936, data=' Monday - Saturday 4:00 PM - 12:00 AM', document=Document(id=829cb8c526265bc03477b109eb89acda01db27d62b51c8fa586ca3c63ec56afd, content: 'Zarpe, Bar, Cocktails, Alcohol, LASENORA@ZARPE.BAR, Monday - Saturday 4:00 PM - 12:00 AM, Sunday - C...', score: 20.497650393518462), context=None, document_offset=ExtractedAnswer.Span(start=51, end=88), context_offset=No

In [ ]:
query = "When is open the restaurant Zi Lounge?"
qa_pipeline.run(
    data={"retriever": {"query": query, "top_k": 3}, "reader": {"query": query, "top_k": 3}}
)

{'reader': {'answers': [ExtractedAnswer(query='When is open the restaurant Zi Lounge?', score=0.766321063041687, data=' Monday - Sunday 11:00 AM - 2:30 AM', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 19.801461834952015), context=None, document_offset=ExtractedAnswer.Span(start=125, end=160), context_offset=None, meta={}),
   ExtractedAnswer(query='When is open the restaurant Zi Lounge?', score=0.6740315556526184, data=' Monday - Saturday 4:00 PM - 12:00 AM', document=Document(id=829cb8c526265bc03477b109eb89acda01db27d62b51c8fa586ca3c63ec56afd, content: 'Zarpe, Bar, Cocktails, Alcohol, LASENORA@ZARPE.BAR, Monday - Saturday 4:00 PM - 12:00 AM, Sunday - C...', score: 16.35872539077387), context=None, document_offset=ExtractedAnswer.Span(start=51, end=88), context_offset=None, meta={}),
   ExtractedAnswer(query='When is open 

In [ ]:
algo_answers = []
for question in QA_dataset_from_LLMs['Questions']:
    # Запуск алгоритма для получения ответа
    result = qa_pipeline.run(data={"retriever": {"query": question, "top_k": 3},
                                   "reader": {"query": question, "top_k": 3}})
    # Добавление ответа в список
    algo_answers.append(result)

In [ ]:
QA_dataset_from_LLMs['algo_answers'] = algo_answers

In [ ]:
QA_dataset_from_LLMs

Questions  \
0                                         1. "What Italian restaurants are there in Playa Hermosa?"   
1                                        2. "What American-style restaurants are there in Liberia?"   
2                                         3. "What French restaurants are there in Playa del Coco?"   
3                                  4. "What vegan-friendly restaurants are there in Playa Hermosa?"   
4                                          5. "What Asian restaurants are there in Playa del Coco?"   
5                                                      6. "What cafes are there in Playa del Coco?"   
6                                              7. "What entertainment venues are there in Liberia?"   
7                  8. "Where can I find beauty or service-related establishments in Playa Hermosa?"   
8                                           9. "What beachfront cafes are there in Playa del Coco?"   
9                   10. "Where can I find entertainment venues with beach access in Playa Hermosa?"   
10                                            11. "What cafes near the beach are there in Liberia?"   
11                12. "Where can I find beauty and spa services with a sea view in Playa del Coco?"   
12                      13. "What family-friendly entertainment venues are there in Playa Hermosa?"   
13                         14. "What restaurants in Playa del Coco are open late into the evening?"   
14                            15. "Which establishments in Playa Ocotal open early in the morning?"   
15                                          16. "Which cafes are open right now in Playa del Coco?"   
16                                             17. "Where can I find a good gift shop in San José?"   
17                                            18. "What are some good places to visit in San José?"   
18                                    19. "Are there any good places to buy souvenirs in San José?"   
19                                           20. "What are some popular art galleries in San José?"   
20                             21. "What are some popular places to visit in San José for culture?"   
21                          22. "What are some popular places to go for entertainment in San José?"   
22                           23. "What are some popular places to visit in Puntarenas for culture?"   
23                                     24. "What are some popular places to visit in Puerto Viejo?"   
24                                                        25. "What are some popular bars in Jacó?"   
25                                          26. "What are some popular shopping centers in Escazú?"   
26                                                 27. "What are some popular theaters in Cartago?"   
27                                                 28. "What are some popular nightclubs in Limón?"   
28                                                   29. "What are some popular parks in Alajuela?"   
29                       30. "What are some popular beaches in Jacó that are suitable for surfing?"   
30                 31. "What are some popular coffee shops in Heredia that serve specialty coffee?"   
31                           32. "What are some popular nightclubs in Limón that play Latin music?"   
32                            33. "What are some popular parks in Alajuela that have a playground?"   
33                          34. "What are some popular theaters in Cartago that host performances?"   
34            35. "What are some popular shopping centers in Escazú that have a variety of stores?"   
35                36. "What are some popular coffee shops in San José that serve specialty coffee?"   
36           37. "What are some popular restaurants in Tamarindo that serve international cuisine?"   
37                         38. "What are some popular coffee shops in Heredia that serve pastries?"   
38                                39. "What are some popular parks in Ala

Работа модели t5 также неудовлетворительна. Нужно поменять подход.

In [ ]:
 pd.set_option('display.max_rows', None)

In [ ]:
df_for_LLM['property_tag_old_2'].value_counts()

property_tag_old_2
Supermarket                                                                                                           14
Beaches                                                                                                                9
Appliance Store                                                                                                        7
Speciality & Gift Shops                                                                                                7
Bank, ATM                                                                                                              5
Pharmacy                                                                                                               4
Hardware Store                                                                                                         3
Gas Station, Gasoline                                                                                                  3
Barbershop                                                                                                             3
Beauty Bar                                                                                                             2
Car Repair                                                                                                             2
EV Charging Station                                                                                                    2
Golf Cart Rental, Golf Cart Repair                                                                                     2
Fitness, Sport                                                                                                         2
Utilities                                                                                                              2
Department Store                                                                                                       2
Cafe, American, Desserts, Coffee, Fast Food, Burgers                                                                   1
Restaurant, International, Kids Menu, Seafood, Meat, Salads, Cocktails, Beer, Wine                                     1
Canteen, International, Pastry, Coffee, Desserts                                                                       1
Cafe, Coffee, Desserts                                                                                                 1
Restaurant, Greek, Mediterranean, Gluten-free, Kids Menu, Seafood, Meat, Alcohol, Salads, Desserts,                    1
Cafe, International, Coffee, Desserts                                                                                  1
Fast Food                                                                                                              1
Restaurant, Italian, Mediterranean, Vegetarian, Vegan, Gluten-free, Seafood, Pizza, Meat, Pasta, Wine                  1
Post Office                                                                                                            1
Airport                                                                                                                1
Hiking, Watefalls, Volcanos                                                                                            1
Parks                                                                                                                  1
Soda, Local, Latin, Casado, Ceviche, Meat, Seafood, Salads                                                             1
Restaurant, Bar, Spanish, Seafood, Pasta, Salads, Meat, Cocktails, Alcohol                                             1
Soda, Local, Latin, Kids Menu, Chifrijo, Ceviche, Seafood, Fast Food, Salads, Burgers, Meat                            1
Bar, Fast Food, Seafood, Meat, Pasta, Pizza, Cocktails                                                                 1
Restaurant, Mediterranean, Gluten-free, Vegan, Salads, Meat, Coffee                                          

Нужно попробовать переработать исходный датасет следующим образом. Объединить все типы заведений в Places to Eat, Adventures и Services, причем по локациям. Так как тексты могут быть длинными, использовать в качестве моделей reader - longformer.

In [ ]:
df_for_LLM['property_location'].value_counts()

property_location
Playa del Coco              97
Liberia                     18
Sardinal                     8
Playa Hermosa                5
Comunidad                    4
Playa Ocotal                 3
no information available     2
Playa Calson de Pobre        1
Playa Panama                 1
Playa Gringo                 1
Playa Tamarindo              1
Playa Penca                  1
Carrillo                     1
Guardia                      1
Bagaces                      1
PANAMA                       1
Canalete                     1
Playa Pez Vela               1
Name: count, dtype: int64

In [ ]:
file_path = '/content/drive/My Drive/df_for_LLM_2.xlsx'
df_for_LLM_2 = pd.read_excel(file_path)

In [ ]:
def concatenate_text(series):
    return ' '.join(series.dropna().astype(str))

# Группировка и агрегация
df_for_LLM_2 = df_for_LLM_2.groupby(['property_location', 'property_type']).agg({
    'name': concatenate_text,
    'property_tag_old_2': concatenate_text,
    'property_email': concatenate_text,
    'property_hours_of_operation': concatenate_text,
    'property_description': concatenate_text,
    'property_phone_number': concatenate_text,
    'combined_text': concatenate_text
}).reset_index()

In [ ]:
df_for_LLM_2

property_location  property_type  \
0                    Bagaces     Adventures   
1                   Canalete        Service   
2                   Carrillo     Adventures   
3                  Comunidad        Service   
4                    Guardia  Places to Eat   
5                    Liberia     Adventures   
6                    Liberia        Service   
7                     PANAMA     Adventures   
8      Playa Calson de Pobre     Adventures   
9               Playa Gringo     Adventures   
10             Playa Hermosa     Adventures   
11             Playa Hermosa  Places to Eat   
12             Playa Hermosa        Service   
13              Playa Ocotal     Adventures   
14              Playa Ocotal        Service   
15              Playa Panama     Adventures   
16               Playa Penca     Adventures   
17            Playa Pez Vela     Adventures   
18           Playa Tamarindo     Adventures   
19            Playa del Coco     Adventures   
20            Playa del Coco  Places to Eat   
21            Playa del Coco        Service   
22                  Sardinal        Service   
23  no information available  Places to Eat   
24  no information available        Service   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       name  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               Thermomania   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             Policia Upala   
2                                                                                                                                                                                                                                                                                                      

In [ ]:
df_for_LLM_2.to_excel('df_for_LLM_3.xlsx', index=False)

In [ ]:
file_path = '/content/drive/My Drive/df_for_LLM_3.xlsx'
df_for_LLM_3 = pd.read_excel(file_path)

In [ ]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

In [ ]:
df_for_LLM_3

property_location  property_type  \
0                    Bagaces     Adventures   
1                   Canalete        Service   
2                   Carrillo     Adventures   
3                  Comunidad        Service   
4                    Guardia  Places to Eat   
5                    Liberia     Adventures   
6                    Liberia        Service   
7                     PANAMA     Adventures   
8      Playa Calson de Pobre     Adventures   
9               Playa Gringo     Adventures   
10             Playa Hermosa     Adventures   
11             Playa Hermosa  Places to Eat   
12             Playa Hermosa        Service   
13              Playa Ocotal     Adventures   
14              Playa Ocotal        Service   
15              Playa Panama     Adventures   
16               Playa Penca     Adventures   
17            Playa Pez Vela     Adventures   
18           Playa Tamarindo     Adventures   
19            Playa del Coco     Adventures   
20            Playa del Coco  Places to Eat   
21            Playa del Coco        Service   
22                  Sardinal        Service   
23  no information available  Places to Eat   
24  no information available        Service   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       name  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               Thermomania   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             Policia Upala   
2                                                                                                                                                                                                                                                                                                      

In [ ]:
QA_dataset_from_LLMs

Questions  \
0                                         1. "What Italian restaurants are there in Playa Hermosa?"   
1                                        2. "What American-style restaurants are there in Liberia?"   
2                                         3. "What French restaurants are there in Playa del Coco?"   
3                                  4. "What vegan-friendly restaurants are there in Playa Hermosa?"   
4                                          5. "What Asian restaurants are there in Playa del Coco?"   
5                                                      6. "What cafes are there in Playa del Coco?"   
6                                              7. "What entertainment venues are there in Liberia?"   
7                  8. "Where can I find beauty or service-related establishments in Playa Hermosa?"   
8                                           9. "What beachfront cafes are there in Playa del Coco?"   
9                   10. "Where can I find entertainment venues with beach access in Playa Hermosa?"   
10                                            11. "What cafes near the beach are there in Liberia?"   
11                12. "Where can I find beauty and spa services with a sea view in Playa del Coco?"   
12                      13. "What family-friendly entertainment venues are there in Playa Hermosa?"   
13                         14. "What restaurants in Playa del Coco are open late into the evening?"   
14                            15. "Which establishments in Playa Ocotal open early in the morning?"   
15                                          16. "Which cafes are open right now in Playa del Coco?"   
16                                             17. "Where can I find a good gift shop in San José?"   
17                                            18. "What are some good places to visit in San José?"   
18                                    19. "Are there any good places to buy souvenirs in San José?"   
19                                           20. "What are some popular art galleries in San José?"   
20                             21. "What are some popular places to visit in San José for culture?"   
21                          22. "What are some popular places to go for entertainment in San José?"   
22                           23. "What are some popular places to visit in Puntarenas for culture?"   
23                                     24. "What are some popular places to visit in Puerto Viejo?"   
24                                                        25. "What are some popular bars in Jacó?"   
25                                          26. "What are some popular shopping centers in Escazú?"   
26                                                 27. "What are some popular theaters in Cartago?"   
27                                                 28. "What are some popular nightclubs in Limón?"   
28                                                   29. "What are some popular parks in Alajuela?"   
29                       30. "What are some popular beaches in Jacó that are suitable for surfing?"   
30                 31. "What are some popular coffee shops in Heredia that serve specialty coffee?"   
31                           32. "What are some popular nightclubs in Limón that play Latin music?"   
32                            33. "What are some popular parks in Alajuela that have a playground?"   
33                          34. "What are some popular theaters in Cartago that host performances?"   
34            35. "What are some popular shopping centers in Escazú that have a variety of stores?"   
35                36. "What are some popular coffee shops in San José that serve specialty coffee?"   
36           37. "What are some popular restaurants in Tamarindo that serve international cuisine?"   
37                         38. "What are some popular coffee shops in Heredia that serve pastries?"   
38                                39. "What are some popular parks in Ala

In [ ]:
# Пример №3, в контенте combined_text то есть содержимое всех столбцов
documents = [
    Document(
        content=f"{row['combined_text']}",

    )
    for _, row in df_for_LLM.iterrows()
]

In [ ]:
# Создаем DocumentStore
document_store = InMemoryDocumentStore()

# Добавляем документы в DocumentStore
document_store.write_documents(documents)

# Создаем InMemoryEmbeddingRetriever
retriever = InMemoryEmbeddingRetriever(document_store=document_store)

In [ ]:
qa_pipeline = Pipeline()

In [ ]:
retriever = InMemoryBM25Retriever(document_store=document_store)
qa_pipeline.add_component(instance=retriever, name="retriever")

In [ ]:
qa_pipeline.add_component(instance=ExtractiveReader(model="deepset/deberta-v3-base-squad2"), name="reader")

In [ ]:
qa_pipeline.connect("retriever", "reader")

🚅 Components
  - retriever: InMemoryBM25Retriever
  - reader: ExtractiveReader
🛤️ Connections
  - retriever.documents -> reader.documents (List[Document])

In [ ]:
algo_answers = []
for question in QA_dataset_from_LLMs['Questions']:
    # Запуск алгоритма для получения ответа
    result = qa_pipeline.run(data={"retriever": {"query": question, "top_k": 3},
                                   "reader": {"query": question, "top_k": 3}})
    # Добавление ответа в список
    algo_answers.append(result)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/992 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/735M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/379 [00:00<?, ?B/s]

spm.model:   0%|          | 0.00/2.46M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/8.65M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/173 [00:00<?, ?B/s]

In [ ]:
QA_dataset_from_LLMs['algo_answers'] = algo_answers

In [ ]:
QA_dataset_from_LLMs

Questions  \
0                                         1. "What Italian restaurants are there in Playa Hermosa?"   
1                                        2. "What American-style restaurants are there in Liberia?"   
2                                         3. "What French restaurants are there in Playa del Coco?"   
3                                  4. "What vegan-friendly restaurants are there in Playa Hermosa?"   
4                                          5. "What Asian restaurants are there in Playa del Coco?"   
5                                                      6. "What cafes are there in Playa del Coco?"   
6                                              7. "What entertainment venues are there in Liberia?"   
7                  8. "Where can I find beauty or service-related establishments in Playa Hermosa?"   
8                                           9. "What beachfront cafes are there in Playa del Coco?"   
9                   10. "Where can I find entertainment venues with beach access in Playa Hermosa?"   
10                                            11. "What cafes near the beach are there in Liberia?"   
11                12. "Where can I find beauty and spa services with a sea view in Playa del Coco?"   
12                      13. "What family-friendly entertainment venues are there in Playa Hermosa?"   
13                         14. "What restaurants in Playa del Coco are open late into the evening?"   
14                            15. "Which establishments in Playa Ocotal open early in the morning?"   
15                                          16. "Which cafes are open right now in Playa del Coco?"   
16                                             17. "Where can I find a good gift shop in San José?"   
17                                            18. "What are some good places to visit in San José?"   
18                                    19. "Are there any good places to buy souvenirs in San José?"   
19                                           20. "What are some popular art galleries in San José?"   
20                             21. "What are some popular places to visit in San José for culture?"   
21                          22. "What are some popular places to go for entertainment in San José?"   
22                           23. "What are some popular places to visit in Puntarenas for culture?"   
23                                     24. "What are some popular places to visit in Puerto Viejo?"   
24                                                        25. "What are some popular bars in Jacó?"   
25                                          26. "What are some popular shopping centers in Escazú?"   
26                                                 27. "What are some popular theaters in Cartago?"   
27                                                 28. "What are some popular nightclubs in Limón?"   
28                                                   29. "What are some popular parks in Alajuela?"   
29                       30. "What are some popular beaches in Jacó that are suitable for surfing?"   
30                 31. "What are some popular coffee shops in Heredia that serve specialty coffee?"   
31                           32. "What are some popular nightclubs in Limón that play Latin music?"   
32                            33. "What are some popular parks in Alajuela that have a playground?"   
33                          34. "What are some popular theaters in Cartago that host performances?"   
34            35. "What are some popular shopping centers in Escazú that have a variety of stores?"   
35                36. "What are some popular coffee shops in San José that serve specialty coffee?"   
36           37. "What are some popular restaurants in Tamarindo that serve international cuisine?"   
37                         38. "What are some popular coffee shops in Heredia that serve pastries?"   
38                                39. "What are some popular parks in Ala

In [ ]:
qa_pipeline = Pipeline()

In [ ]:
retriever = InMemoryBM25Retriever(document_store=document_store)
qa_pipeline.add_component(instance=retriever, name="retriever")

In [ ]:
qa_pipeline.add_component(instance=ExtractiveReader(model="sjrhuschlee/flan-t5-base-squad2"), name="reader")

In [ ]:
qa_pipeline.connect("retriever", "reader")

🚅 Components
  - retriever: InMemoryBM25Retriever
  - reader: ExtractiveReader
🛤️ Connections
  - retriever.documents -> reader.documents (List[Document])

In [ ]:
qa_pipeline.run(data={"retriever": {"query": QA_dataset_from_LLMs['Questions'][0],"top_k": 3}, "reader": {"query": QA_dataset_from_LLMs['Questions'][0], "top_k":3}})

config.json:   0%|          | 0.00/1.63k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/2.35k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/21.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.23k [00:00<?, ?B/s]

{'reader': {'answers': [ExtractedAnswer(query='1. "What Italian restaurants are there in Playa Hermosa?"', score=0.6050990223884583, data=' Pizza', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 18.382970355806773), context=None, document_offset=ExtractedAnswer.Span(start=51, end=57), context_offset=None, meta={}),
   ExtractedAnswer(query='1. "What Italian restaurants are there in Playa Hermosa?"', score=0.5684860944747925, data='Zi Lounge', document=Document(id=e8a323a4533b246c32c4f3b40c1c583c7684cad1b757abb5e4bd8b211c473ac4, content: 'Zi Lounge, Restaurant, Bar, International, Seafood, Pizza, Pasta, Meat, Steak, Salads, Cocktails, Al...', score: 18.382970355806773), context=None, document_offset=ExtractedAnswer.Span(start=0, end=9), context_offset=None, meta={}),
   ExtractedAnswer(query='1. "What Italian restaurants are t